In [1]:
!brew install fetch
!mkdir temp/gotenberg
!fetch --branch=main --source-path=/docs --repo=https://github.com/gotenberg/gotenberg.dev temp/gotenberg
%pip install markdown
%pip install python-frontmatter

zsh:1: command not found: brew
mkdir: cannot create directory ‘temp/gotenberg’: No such file or directory
zsh:1: command not found: fetch
Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.
Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


## Create Book if it doesn't exist


In [29]:
import requests
import os

url = "https://donavanaldrich.com/api/bookstack/books"

payload = {
    "name":
    "python-cheatsheet",
    "description":
    "python-cheatsheet",
    "tags": [{
        "name": "Platform",
        "value": "Python"
    }, {
        "name": "Category",
        "value": "Code"
    }, {
        "name": "Type",
        "value": "Cheatsheet"
    }]
}
headers = {
    "X-API-KEY": os.getenv(X_API_KEY),
    "Authorization": os.getenv(BOOKSTACK_API_TOKEN)
}

response = requests.request("POST", url, json=payload, headers=headers)

print(response.text)

{"name":"python-cheatsheet","description":"python-cheatsheet","created_by":1,"updated_by":1,"owned_by":1,"slug":"python-cheatsheet","updated_at":"2022-08-10T00:14:32.000000Z","created_at":"2022-08-10T00:14:32.000000Z","id":3}


## Create Chapters


### List folders to map to chapters


In [1]:
import os

dir = os.listdir("../temp/python-cheatsheets")

print(dir)

['cheatsheet', 'modules', 'builtin']


In [23]:
import requests

chapters = ['cheatsheet', 'modules', 'builtin']

url = "https://donavanaldrich.com/api/bookstack/chapters"

for chapter_name in chapters:

    payload = {
        "book_id": 2,
        "name": chapter_name,
        "description": chapter_name,
        "tags": [{
            "name": "chapter",
            "value": chapter_name
        }]
    }
    headers = {
        "X-API-KEY": os.getenv(X_API_KEY),
        "Authorization": os.getenv(BOOKSTACK_API_TOKEN)
    }

    response = requests.request("POST", url, json=payload, headers=headers)
    response_json = response.json()
    chapter_id = response_json['id']
    print(chapter_id)

18
19
20


## Add Pages


In [1]:
from pathlib import Path
import requests
import frontmatter

chapters = ['cheatsheet', 'modules', 'builtin']

headers = {
    "X-API-KEY": os.getenv(X_API_KEY),
    "Authorization": os.getenv(BOOKSTACK_API_TOKEN)
}

url = "https://donavanaldrich.com/api/bookstack/books"

payload = {
    "name":
    "python-cheatsheet",
    "description":
    "python-cheatsheet",
    "tags": [{
        "name": "Platform",
        "value": "Python"
    }, {
        "name": "Category",
        "value": "Code"
    }, {
        "name": "Type",
        "value": "Cheatsheet"
    }]
}

response = requests.request("POST", url, json=payload, headers=headers)
response_json = response.json()
book_id = response_json['id']

# book_id = xs
#
for chapter in chapters:
    payload = {
        "book_id": book_id,
        "name": chapter,
        "description": chapter,
        "tags": [{
            "name": "chapter",
            "value": chapter
        }]
    }
    url = "https://donavanaldrich.com/api/bookstack/chapters"
    response = requests.request("POST", url, json=payload, headers=headers)
    response_json = response.json()
    chapter_id = response_json['id']
    print(chapter_id)

    for page in Path('../temp/python-cheatsheets/' + chapter).iterdir():
        url = "https://donavanaldrich.com/api/bookstack/pages"
        with open(page, 'r') as f:
            metadata, content = frontmatter.parse(f.read())
            try:
                page_name = metadata['title']
            except:
                page_name = str(page)
            payload = {
                "book_id": book_id,
                "chapter_id": chapter_id,
                "name": page_name,
                "markdown": content,
                "tags": [{
                    "name": "chapter",
                    "value": chapter
                }]
            }
            response = requests.request("POST",
                                        url,
                                        json=payload,
                                        headers=headers)

        # print(response.text)


NameError: name 'X_API_KEY' is not defined

### Development/Sandboxing


In [28]:
# for page in Path('../temp/python-cheatsheets/' + chapter).iterdir():
page = '../temp/python-cheatsheets/cheatsheet/debugging.md'
url = "https://donavanaldrich.com/api/bookstack/pages"

with open(page, 'r') as f:
    # text = f.read()
    # post = frontmatter.load(page)
    metadata, content = frontmatter.parse(f.read())
print(content)

# Python Debugging

<base-disclaimer>
  <base-disclaimer-title>
    <a target="_blank" href="https://en.wikipedia.org/wiki/Debugging">Finding and resolving bugs</a>
  </base-disclaimer-title>
  <base-disclaimer-content>
    In computer programming and software development, debugging is the process of finding and resolving bugs (defects or problems that prevent correct operation) within computer programs, software, or systems.
  </base-disclaimer-content>
</base-disclaimer>

## Raising Exceptions

Exceptions are raised with a raise statement. In code, a raise statement consists of the following:

- The `raise` keyword
- A call to the `Exception()` function
- A string with a helpful error message passed to the `Exception()` function

```python
>>> raise Exception('This is the error message.')
# Traceback (most recent call last):
#   File "<pyshell#191>", line 1, in <module>
#     raise Exception('This is the error message.')
# Exception: This is the error message.
```

Typically, it’s th

## Reference

### Payloads

#### book

```json
{
  "name": "python-cheatsheet",
  "description": "python-cheatsheet",
  "tags": [
    { "name": "Platform", "value": "Python" },
    { "name": "Category", "value": "Code" },
    { "name": "Type", "value": "Cheatsheet" }
  ]
}
```

#### Chapter

```json
{
  "book_id": 1,
  "name": "My fantastic new chapter",
  "description": "This is a great new chapter that I've created via the API",
  "tags": [
    { "name": "Category", "value": "Top Content" },
    { "name": "Rating", "value": "Highest" }
  ]
}
```

#### Page

```json
{
  "book_id": 1,
  "name": "My API Page",
  "markdown": "<p>my new API page</p>",
  "tags": [
    { "name": "Category", "value": "Not Bad Content" },
    { "name": "Rating", "value": "Average" }
  ]
}
```


In [12]:
import frontmatter  # https://pypi.org/project/python-frontmatter/
import markdown


def parse_markdown(filepath):
    # markdown_parser = markdown.Markdown(extensions=markdown_extensions)
    file_parts = frontmatter.load(filepath)

    return {
        # 'html': markdown_parser.convert(file_parts.content),
        'metadata': file_parts.metadata
    }


parse_markdown('../temp/python-cheatsheets/cheatsheet/debugging.md')

AttributeError: module 'frontmatter' has no attribute 'load'